In [130]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import os
import re
from random import sample as random_sample

%matplotlib inline

In [131]:
#load data with fixed mutations removed
raw = pd.read_csv('/Users/chrisgraves/Documents/Yeast_data/Sequencing/saved_dfs/combined_filtered.csv')
num_alleles = df.shape[0]/6
print('There are %d alleles' %num_alleles)
raw.head()


There are 39891 alleles


Chromosome  Position               Alt  Time              Ref  Is_repeat  \
0          I      5068  ATTTTTTTTTTTTTTC     1  ATTTTTTTTTTTTTC          1   
1          I      5068  ATTTTTTTTTTTTTTC     3  ATTTTTTTTTTTTTC          1   
2          I      5068  ATTTTTTTTTTTTTTC     5  ATTTTTTTTTTTTTC          1   
3          I      5068  ATTTTTTTTTTTTTTC     7  ATTTTTTTTTTTTTC          1   
4          I      5068  ATTTTTTTTTTTTTTC     9  ATTTTTTTTTTTTTC          1   

   Read_depth  Num_ref  Num_alt  Freq_ref  Freq_alt  Qual_ref  Qual_alt  \
0         NaN      NaN        0       NaN         0       NaN       NaN   
1         NaN      NaN        0       NaN         0       NaN       NaN   
2         NaN      NaN        0       NaN         0       NaN       NaN   
3         NaN      NaN        0       NaN         0       NaN       NaN   
4         NaN      NaN        0       NaN         0       NaN       NaN   

  Treatment  Strain  
0         C       1  
1         C       1  
2         C       1  
3         C       1  
4         C       1

In [132]:
#remove variants falling in repeats (very likely sequencing errors)

df = raw[raw['Is_repeat']==0]

after_filter = df.shape[0]/6
print('There are %d alleles, %d were removed by filter' %(after_filter,num_alleles-after_filter))


There are 39891 alleles, 0 were removed by filter


In [133]:
def entropy(df_subset):
    strain_df = df_subset.groupby(['Treatment','Strain'])
    info = 0
    nmuts = df_subset.shape[0]/6
    for name, data in strain_df:
        xi = (float(data.shape[0]/6))/float(nmuts)
        info = info+xi+np.log2(xi)
        return(-info)



In [134]:
#create dictionary to change chromosome names
chrom_key = list(['I','II','III','IV','V','VI','VII','VIII','IX','X','XI','XII','XIII','XIV','XV','XVI'])
chrom_len = list((230218,813184,316620,1531933,576874,270161,1090940,562643,439888,745751,666816,1078177,924431,784333,1091291,948066))

chrom_dict = dict(zip(chrom_key,chrom_len))

In [153]:
def get_muts(df,chrom,start,end):
    out = df[((df['Chromosome']==chrom) & (df['Position'] >= start) & (df['Position'] <= end))]
    return(out)

In [163]:

def cluster_finder(start_0,win):

    counter = 0
    windows = pd.DataFrame(columns = ['Chrom','Start','End','N_muts','N_H','N_C','Qual','Depth','Info'])

    for chrom in chrom_key:
        win_count = 0
        starts = np.arange(start=start_0,stop=chrom_dict[chrom],step=win)
        stops = starts+win-1
        stops[len(stops)-1] = chrom_dict[chrom]
    
        for start in starts:
            stop = stops[win_count]
            win_count = win_count+1
            df_region = get_muts(df,chrom,start,stop)
        
            if df_region.shape[0] > 0:
                nmuts = df_region.shape[0]/6
                info = entropy(df_region)
                n_H = df_region[df_region['Treatment']=='H'].shape[0]/6
                n_C = nmuts-n_H
                mean_qual = df_region['Qual_alt'].mean()
                mean_depth = df_region['Read_depth'].mean()
            else:
                nmuts = 0
                info = np.nan
                n_H = 0
                n_C = 0
                mean_qual = np.nan
                mean_depth = np.nan
            
            windows.loc[counter] = (chrom,start,stop,nmuts,n_H,n_C,mean_qual,mean_depth,info)
            counter=counter+1
    windows['Var_skew'] = (windows['N_C']-windows['N_H'])/windows['N_muts']
    return(windows)



In [164]:
win = 1000
windows = cluster_finder(0,win)

num_windows = windows.shape[0]
print('Reporting %d windows of %d bps length with variants' %(num_windows,win))
windows.head()

Reporting 12079 windows of 1000 bps length with variants


Chrom  Start   End  N_muts  N_H  N_C  Qual  Depth      Info  Var_skew
0     I      0   999       5    4    1   6.7      9  2.121928      -0.6
1     I   1000  1999       0    0    0   NaN    NaN       NaN       NaN
2     I   2000  2999       0    0    0   NaN    NaN       NaN       NaN
3     I   3000  3999       0    0    0   NaN    NaN       NaN       NaN
4     I   4000  4999       0    0    0   NaN    NaN       NaN       NaN

In [165]:
win = 1000
windows2 = cluster_finder(500,win)

num_windows = windows2.shape[0]
print('Reporting %d windows of %d bps length with variants' %(num_windows,win))
windows2.head()

Reporting 12071 windows of 1000 bps length with variants


Chrom  Start   End  N_muts  N_H  N_C Qual Depth Info  Var_skew
0     I    500  1499       0    0    0  NaN   NaN  NaN       NaN
1     I   1500  2499       0    0    0  NaN   NaN  NaN       NaN
2     I   2500  3499       0    0    0  NaN   NaN  NaN       NaN
3     I   3500  4499       0    0    0  NaN   NaN  NaN       NaN
4     I   4500  5499       0    0    0  NaN   NaN  NaN       NaN

In [166]:
combined = pd.concat([windows,windows2])
combined.shape

(24150, 10)

In [182]:
skewed = combined[(np.absolute(combined['Var_skew'])>0.7) & (combined['Qual']>20) & (combined['Depth'] >15) & (combined['N_muts'] > 1)]
print(skewed.shape)
skewed

(15, 10)


Chrom   Start     End  N_muts  N_H  N_C     Qual    Depth     Info  \
771     II  540000  540999       3    0    3  29.9111  15.6667  1.25163   
2022    IV  660000  660999       2    0    2  37.6444       38      0.5   
3866   VII  124000  124999       7    7    0  36.3628     70.8   2.6645   
3867   VII  125000  125999       2    2    0  38.6663       54      0.5   
3870   VII  128000  128999       3    3    0  36.6457  37.2857  1.25163   
5436    IX   40000   40999       2    0    2   20.125       17      0.5   
8632  XIII  304000  304999       5    5    0  35.8947     45.7  2.12193   
9979   XIV  726000  726999       3    3    0  34.0889     47.2  1.25163   
770     II  540500  541499       3    0    3  29.9111  15.6667  1.25163   
2019    IV  659500  660499       2    0    2  37.6444       38      0.5   
3863   VII  124500  125499       8    8    0  36.5349  69.7727    2.875   
3867   VII  128500  129499       2    2    0  35.4513     34.4      0.5   
5433    IX   40500   41499       2    0    2   20.125       17      0.5   
8627  XIII  303500  304499       5    5    0  35.8947     45.7  2.12193   
9973   XIV  725500  726499       3    3    0  34.0889     47.2  1.25163   

      Var_skew  
771          1  
2022         1  
3866        -1  
3867        -1  
3870        -1  
5436         1  
8632        -1  
9979        -1  
770          1  
2019         1  
3863        -1  
3867        -1  
5433         1  
8627        -1  
9973        -1

In [185]:
multiple_hits = combined[(np.absolute(combined['N_muts'])>2) & (combined['Qual']>20) & (combined['Depth'] >15) & (combined['N_muts'] > 1)]
print(multiple_hits.shape)
multiple_hits

(42, 10)


Chrom    Start      End  N_muts  N_H  N_C     Qual    Depth     Info  \
12        I    12000    12999      57   28   29  33.3497  161.706   4.7978   
189       I   189000   189999      35   19   16  30.8023  49.7551  4.07214   
232      II     1000     1999       5    4    1  37.4099     64.6  2.12193   
771      II   540000   540999       3    0    3  29.9111  15.6667  1.25163   
3866    VII   124000   124999       7    7    0  36.3628     70.8   2.6645   
3870    VII   128000   128999       3    3    0  36.6457  37.2857  1.25163   
4272    VII   530000   530999      54   27   27  23.9507  16.0488  4.11437   
4561    VII   819000   819999      54   28   26  36.6079  18.2901  4.71785   
5168   VIII   335000   335999      20   10   10  33.8418  96.7442  4.27193   
5389   VIII   556000   556999      26   12   14  26.8013  24.6552  4.66198   
5395   VIII   562000   562643     270  130  140  26.2208  32.5651  3.92639   
5421     IX    25000    25999       9    6    3  27.2745  62.0526  1.25163   
5788     IX   392000   392999      28   11   17   22.527  35.7949  4.77164   
6551      X   715000   715999      88   46   42  30.0422  30.0992   5.4367   
7260    XII    11000    11999      54   30   24  33.8672  28.7581  4.71785   
8632   XIII   304000   304999       5    5    0  35.8947     45.7  2.12193   
8903   XIII   575000   575999       7    4    3  38.0072  51.1429   2.6645   
9236   XIII   908000   908999      15    6    9  30.9916  27.7692  2.12193   
9979    XIV   726000   726999       3    3    0  34.0889     47.2  1.25163   
10066    XV    28000    28999      23   10   13  34.8528    62.34  4.48008   
10747    XV   709000   709999      52   24   28   28.121   20.237  4.05778   
12        I    12500    13499      57   28   29  33.3497  161.706   4.7978   
188       I   188500   189499      35   19   16  30.8023  49.7551  4.07214   
770      II   540500   541499       3    0    3  29.9111  15.6667  1.25163   
3863    VII   124500   125499       8    8    0  36.5349  69.7727    2.875   
4268    VII   529500   530499      74   39   35  23.4325  15.8128  4.58395   
4558    VII   819500   820499      68   35   33  33.7894  17.3103  4.45838   
5165   VIII   335500   336499      20   10   10  33.8418  96.7442  4.27193   
5391   VIII   561500   562499     152   75   77  23.3221   41.574   4.1953   
5418     IX    25500    26499       7    5    2    27.79  66.5294  1.52164   
5601     IX   208500   209499       5    2    3    23.04     16.2  2.12193   
6547      X   714500   715499      88   46   42  30.0422  30.0992   5.4367   
7256    XII    10500    11499      81   46   35  29.5654  24.3421  5.31516   
8310    XII  1064500  1065499       3    2    1  21.2444  16.3333  1.25163   
8627   XIII   303500   304499       5    5    0  35.8947     45.7  2.12193   
8898   XIII   574500   575499       7    4    3  38.0072  51.1429   2.6645   
9231   XIII   907500   908499      10    2    8   30.725    19.85  1.43697   
9232   XIII   908500   909499       5    4    1  31.8804  54.1667  2.12193   
9254    XIV     6500     7499      52   27   25  30.3394  18.8941  5.68121   
9973    XIV   725500   726499       3    3    0  34.0889     47.2  1.25163   
10060    XV    28500    29499      20   10   10  36.7583  65.7021  4.27193   
10741    XV   709500   710499      18   10    8  30.0077  57.8333  4.11437   

       Var_skew  
12     0.017544  
189   -0.085714  
232   -0.600000  
771    1.000000  
3866  -1.000000  
3870  -1.000000  
4272   0.000000  
4561  -0.037037  
5168   0.000000  
5389   0.076923  
5395   0.037037  
5421  -0.333333  
5788   0.214286  
6551  -0.045455  
7260  -0.111111  
8632  -1.000000  
8903  -0.142857  
9236   0.200000  
9979  -1.000000  
10066  0.130435  
10747  0.076923  
12     0.017544  
188   -0.085714  
770    1.000000  
3863  -1.000000  
4268  -0.054054  
4558  -0.029412  
5165   0.000000  
5391   0.013158  
5418  -0.428571  
5601   0.200000  
6547  -0.045455  
7256  -0.135802  
8310  -0.333333  
8627  -1.000000  
889

In [192]:
ara1 = get_muts(df,'II',71800,73000)
ara1

Empty DataFrame
Columns: [Chromosome, Position, Alt, Time, Ref, Is_repeat, Read_depth, Num_ref, Num_alt, Freq_ref, Freq_alt, Qual_ref, Qual_alt, Treatment, Strain]
Index: []

In [186]:
sub_df = multiple_hits

counter=0
for row in sub_df.itertuples():
    if counter == 0:
        allele_clusters = df[((df['Chromosome']==row.Chrom) & (df['Position'] >= row.Start) & (df['Position'] <= row.End))]
    else:
        temp = df[((df['Chromosome']==row.Chrom) & (df['Position'] >= row.Start) & (df['Position'] <= row.End))]
        allele_clusters = pd.concat([allele_clusters,temp],ignore_index=True)
    counter=counter+1
#remove duplicate entries due to window overlap

nrows = allele_clusters.shape[0]
allele_clusters = allele_clusters.drop_duplicates()
n_removed = nrows - allele_clusters.shape[0]

print('Removed %d duplicate rows' %n_removed )

num_alleles = allele_clusters.shape[0]/6
print('There are %d alleles' %num_alleles)

Removed 3546 duplicate rows
There are 948 alleles


In [187]:
allele_clusters.head()

Chromosome  Position Alt  Time Ref  Is_repeat  Read_depth  Num_ref  Num_alt  \
0          I     12620   C     1   T          0         NaN      NaN        0   
1          I     12620   C     3   T          0         NaN      NaN        0   
2          I     12620   C     5   T          0         319      247       71   
3          I     12620   C     7   T          0         NaN      NaN        0   
4          I     12620   C     9   T          0         NaN      NaN        0   

   Freq_ref  Freq_alt   Qual_ref   Qual_alt Treatment  Strain  
0       NaN   0.00000        NaN        NaN         C       1  
1       NaN   0.00000        NaN        NaN         C       1  
2   0.77673   0.22327  36.813765  34.366197         C       1  
3       NaN   0.00000        NaN        NaN         C       1  
4       NaN   0.00000        NaN        NaN         C       1

In [112]:
allele_groups = allele_clusters.groupby(['Chromosome','Position','Alt','Treatment','Strain'])

nrows = np.ceil(num_alleles/float(4))

counter = 1
fig = plt.figure(figsize=(56,nrows*10))
for name, allele in allele_groups:
    N = np.array(allele['Num_alt'])+np.array(allele['Num_ref'])

    x = list(allele['Time'])
    y = list(allele['Freq_alt'])
    err = 1.96*np.sqrt(np.divide((np.ones(6)-y)*y,N))
    qual = list(allele['Qual_alt'])

    ref = allele['Ref'].iloc[0]
    alt = allele['Alt'].iloc[0]
    treatment = allele['Treatment'].iloc[0]
    strain = str(allele['Strain'].iloc[0])
    chrom = allele['Chromosome'].iloc[0]
    pos = str(int(allele['Position'].iloc[0]))

    
    plt.subplot(nrows,4,counter)
    plt.ylabel('Frequency',fontsize=26,fontweight='bold')
    plt.xlabel('Time',fontsize=26,fontweight='bold')
    plt.ylim([-0.1,1.2])
    plt.yticks([0.0,0.2,0.4,0.6,0.8,1.0],size=24,fontweight='bold')
    plt.xlim([0,14])
    plt.xticks([0,2,4,6,8,10,12,14],size=24,fontweight='bold')
    plt.scatter(x,y,s=800,c=qual,cmap='YlOrRd')
    plt.clim(0,40)
    plt.style.use('bmh')
    plt.title('Strain: %s%s \n Chromosome %s \n Position %s \n %s \n to %s' %(treatment,strain,chrom,pos,ref,alt), fontsize=28,fontweight='bold')

    cb = plt.colorbar()
    cb.set_label(label='Quality score',fontsize=26,weight='bold')
    cb.set_ticks([0,5,10,15,20,25,30,35,40])
    cb.ax.tick_params(labelsize=24)
        
    (_, caps, _) = plt.errorbar(x,y,yerr=err,ls='None',color='k',capsize=5)
    for cap in caps:
        cap.set_markeredgewidth(2)

    for i in range(len(x)):
        if not np.isnan(N[i]):
            plt.text(x[i],1.1,int(N[i]),ha='center',fontsize = 23, fontweight='bold',bbox=dict(facecolor='none', edgecolor='black', boxstyle='round'))
        
    plt.tight_layout()
        
    counter = counter+1